In [1]:
import numpy as np
import pandas as pd
from scipy import interpolate
import sympy as sp
import re
import sqlalchemy as db
import CMSHullCalc as cms

import plotly.express as px
import plotly.offline
import plotly.graph_objects as go

3386240.145392972


In [2]:
engine = db.create_engine("mssql+pyodbc:///?odbc_connect=Driver={SQL Server};Server=192.168.11.102;Database=IDPM;Trusted_Connection=True;")

# SWAPTION

### Importing the Data from CSV

In [3]:
Swaption = pd.read_csv(r'C:\Users\rrenard\Desktop\CMS_data\USDSwaption20230331.csv', index_col= 0)

### Plotting the imported data to check for consistency (Bloomberg)

In [4]:
fig = px.line(Swaption.T,labels={"value": "Volatility (anualized)",
                               "index": "Tenor",
                               }, title= 'Quote vs Tenor at Fixed Expiry', template= 'plotly_dark')
fig.show()

In [5]:
fig = px.line(Swaption,labels={"value": "Volatility (anualized)",
                             "Expiry": "Expiry",
                               }, title= 'Quote vs Expiry at Fixed Tenor',template= 'plotly_dark')
fig.show()

In [6]:
fig = go.Figure(data=[go.Surface(z= Swaption.values, x = Swaption.columns, y = Swaption.index)])
fig.update_layout(template = 'plotly_dark',title='3D Surface Swaption Volatility (anualized)', autosize=True,
                  width=800, height=600, margin=dict(l=120, r=120, b=65, t=90), scene = dict(xaxis_title ='Tenor', yaxis_title = 'Expiry', zaxis_title = 'Volatility'))
fig.show()

### Interpolation

In [7]:
# Tenor Data cleaning 
tenor = np.array(Swaption.columns)
tenor_list = str([Swaption.columns])

# Split the tenor to extract the numbers only
TenorNum = np.array(re.findall(r'\d+', tenor_list))

# Extract the Volatility from the DataFrame
SwaptionVols = np.array(Swaption.values)  

# Iterate over the numbers of arrays in SwaptionVols (20) to get the interpolation coefficients
SwaptionVolCoeffCubSpline = []
for i in range(len(SwaptionVols)): # CubicSpline Coefficients
    SwaptionVolCoeffCubSpline.append(interpolate.CubicSpline(TenorNum, SwaptionVols[i]))

SwaptionVolCoeffAkimaSpline = []
for i in range(len(SwaptionVols)): # Akima Coefficients
    SwaptionVolCoeffAkimaSpline.append(interpolate.Akima1DInterpolator(TenorNum, SwaptionVols[i]))
    
# Define New Tenor for the interpolation
NewTenor = np.linspace(1,30,1000)

# Find the interpolated Swaption vol for the new tenor
SwaptionVolCubSpline = []
for i in range(len(SwaptionVolCoeffCubSpline)): # CubicSpline interpolated Swaption vol
    SwaptionVolCubSpline.append(SwaptionVolCoeffCubSpline[i](NewTenor))

SwaptionVolAkima = []
for i in range(len(SwaptionVolCoeffAkimaSpline)): # Akima interpolated Swaption vol
    SwaptionVolAkima.append(SwaptionVolCoeffAkimaSpline[i](NewTenor))


#### CubicSpline

In [8]:
fig = px.line(None,NewTenor, SwaptionVolCubSpline, labels={'value': 'Volatility (anualized)',
                                                           'x': 'Tenor'}, template= 'plotly_dark')
fig.show()

#### Akima

In [9]:
fig = px.line(None,NewTenor, SwaptionVolAkima, labels={'value': 'Volatility (anualized)',
                                                           'x': 'Tenor'}, template= 'plotly_dark')
fig.show()

# Caps

### Import the Data

In [10]:
Cap = pd.read_csv(r'C:\Users\rrenard\Desktop\CMS_data\USCAPVol20230331.csv', index_col= 0)

### Plotting the imported data to check for consistency (Bloomberg)

In [11]:
fig = px.line(Cap,labels={"value": "Volatility (anualized)",
                               "index": "Tenor",
                               }, title= 'Quote vs Tenor at Fixed Strike', template= 'plotly_dark')
fig.show()

In [12]:
fig = px.line(Cap.T,labels={"value": "Volatility (anualized)",
                               "index": "Strikes",
                               }, title= 'Quote vs Strike at Fixed Tenor', template= 'plotly_dark')
fig.show()

In [13]:
fig = go.Figure(data=[go.Surface(z= Cap.values, x = Cap.columns, y = Cap.index)])
fig.update_layout(template= 'plotly_dark', title='3D Surface Cap Volatility (anualized)', autosize=True,
                  width=800, height=600,
                  margin=dict(l=120, r=120, b=65, t=90), scene = dict(xaxis_title ='Strikes', yaxis_title = 'Tenor', zaxis_title = 'Volatility'))
fig.show()

### Interpolation

In [14]:
# Cap Tenor Data cleaning 
TenorCap = np.array(Cap.index)
TenorCap_list = str([Cap.index])

# Split the Cap tenor to extract the numbers only
TenorCNum = np.array(re.findall(r'\d+', TenorCap_list))

# Extract the Cap Volatilty from the DataFrame
CapVol = np.array(Cap.values.T)

# Iterate over the numbers of arrays in CapVol (12) to get the interpolation coefficients
CapVolCoeffCubSpline = []
for i in range(len(CapVol)): # CubicSpline Coefficients
    CapVolCoeffCubSpline.append(interpolate.CubicSpline(TenorCNum, CapVol[i]))

CapVolCoeffAkimaSpline = [] # Akima Coefficients
for i in range(len(CapVol)):
    CapVolCoeffAkimaSpline.append(interpolate.Akima1DInterpolator(TenorCNum, CapVol[i]))

# Define New Cap Tenor for the interpolation
CapNewTenor = np.linspace(1,20,1000)

# Find the interpolated Cap Vol for the new tenor
CapVolCubSpline = []
for i in range(len(CapVolCoeffCubSpline)): # CubicSpline interpolated Cap Vol
    CapVolCubSpline.append(CapVolCoeffCubSpline[i](CapNewTenor))

CapVolAkima = []
for i in range(len(CapVolCoeffAkimaSpline)): # Akima interpolated Cap Vol
    CapVolAkima.append(CapVolCoeffAkimaSpline[i](CapNewTenor))

#### CubicSpline

In [15]:
fig = px.line(None,CapNewTenor, CapVolCubSpline, template= 'plotly_dark')
fig.show()

#### Akima

In [16]:
fig = px.line(None,CapNewTenor, CapVolAkima, template= 'plotly_dark')
fig.show()

# CMS Valuation

##### Extract the list of volatilities from the swaption file

In [17]:
vols = pd.read_excel(r'C:\Users\rrenard\Desktop\CMS_data\VolsForCalc.xlsx', index_col=0)

In [103]:
discount_factor = cms.discount_factor_libor['Discount'].to_list()
discount_factor = np.array(discount_factor)
discount_factor = np.delete(discount_factor, 0)

In [102]:
par_swap_rate_list = []
for i in range(0, 10):
    par_swap_rate = (1 - discount_factor[i])/ sum(discount_factor[:i+1])
    par_swap_rate_list.append(par_swap_rate)

par_swap_rate_list

[0.027160022540780187,
 0.025360721887256608,
 0.02334656082409088,
 0.021933122298276837,
 0.02086219486350329,
 0.01999541851548192,
 0.019356916652488294,
 0.018877454563578,
 0.01851150468931692,
 0.01823616339040887]

#### Result

In [ ]:
cms.swap_value_no_timing(10000000, 2.5, 0.5, 5, 0.05, 0.05, 0.05, list(vols['Swaption']))

154838.53737389686